## Install TensorTrade

In [1]:
#!python3 -m pip install git+https://github.com/tensortrade-org/tensortrade.git

## Setup Data Fetching

In [2]:
import pandas as pd
import tensortrade.env.default as default

from tensortrade.data.cdd import CryptoDataDownload
from tensortrade.feed.core import Stream, DataFeed
from tensortrade.oms.exchanges import Exchange
from tensortrade.oms.services.execution.simulated import execute_order
from tensortrade.oms.instruments import USD, BTC, ETH
from tensortrade.oms.wallets import Wallet, Portfolio
from tensortrade.agents import DQNAgent

%matplotlib inline

In [3]:
from tensortrade.data.cdd import CryptoDataDownload

import pandas as pd
import numpy as np

def prepare_data(df):
    df['volume'] = np.int64(df['volume'])
    df['date'] = pd.to_datetime(df['date'])
    df.sort_values(by='date', ascending=True, inplace=True)
    df.reset_index(drop=True, inplace=True)
    df['date'] = df['date'].dt.strftime('%Y-%m-%d %I:%M %p')
    return df

def fetch_data():
    cdd = CryptoDataDownload()
    bitfinex_data = cdd.fetch("Bitfinex", "USD", "BTC", "1h")
    bitfinex_data = bitfinex_data[['date', 'open', 'high', 'low', 'close', 'volume']]
    bitfinex_data = prepare_data(bitfinex_data)
    return bitfinex_data

def load_csv(filename):
    df = pd.read_csv('data/' + filename, skiprows=1)
    df.drop(columns=['symbol', 'volume_btc'], inplace=True)

    # Fix timestamp from "2019-10-17 09-AM" to "2019-10-17 09-00-00 AM"
    df['date'] = df['date'].str[:14] + '00-00 ' + df['date'].str[-2:]

    return prepare_data(df)

In [4]:
data = fetch_data()
data

date          open         high      low         close  \
0      2018-05-15 06:00 AM   8723.800000   8793.00000   8714.9   8739.000000   
1      2018-05-15 07:00 AM   8739.000000   8754.80000   8719.3   8743.000000   
2      2018-05-15 08:00 AM   8743.000000   8743.10000   8653.2   8723.700000   
3      2018-05-15 09:00 AM   8723.700000   8737.80000   8701.2   8708.100000   
4      2018-05-15 10:00 AM   8708.100000   8855.70000   8695.8   8784.400000   
...                    ...           ...          ...      ...           ...   
32721  2022-02-06 08:00 PM  41767.000000  41788.78777  41551.0  41618.346698   
32722  2022-02-06 09:00 PM  41619.214072  41752.00000  41594.0  41700.000000   
32723  2022-02-06 10:00 PM  41702.000000  41747.00000  41593.0  41641.000000   
32724  2022-02-06 11:00 PM  41637.000000  42739.00000  41549.0  42412.000000   
32725  2022-02-07 12:00 AM  42421.823872  42522.00000  41701.0  41778.000000   

         volume  
0       8988053  
1       2288904  
2       8891773  
3       2054868  
4      17309722  
...         ...  
32721   1592764  
32722   1654274  
32723   1828751  
32724  33461774  
32725  10482068  

[32726 rows x 6 columns]

In [5]:
from sklearn.model_selection import train_test_split

def split_data(data):
    X = data.copy()
    y = X['close'].pct_change()

    X_train_test, X_valid, y_train_test, y_valid = \
        train_test_split(data, data['close'].pct_change(), train_size=0.67, test_size=0.33, shuffle=False)

    X_train, X_test, y_train, y_test = \
        train_test_split(X_train_test, y_train_test, train_size=0.50, test_size=0.50, shuffle=False)

    return X_train, X_test, X_valid, y_train, y_test, y_valid

In [6]:
X_train, X_test, X_valid, y_train, y_test, y_valid = \
    split_data(data)

import os
cwd = os.getcwd()
train_csv = os.path.join(cwd, 'train.csv')
test_csv = os.path.join(cwd, 'test.csv')
valid_csv = os.path.join(cwd, 'valid.csv')
X_train.to_csv(train_csv, index=False)
X_test.to_csv(test_csv, index=False)
X_valid.to_csv(valid_csv, index=False)

## Create features with the feed module

In [7]:
import numpy as np
import ta as ta1
import pandas_ta as ta

def rsi(price: 'pd.Series[pd.Float64Dtype]', period: float) -> 'pd.Series[pd.Float64Dtype]':
    r = price.diff()
    upside = np.minimum(r, 0).abs()
    downside = np.maximum(r, 0).abs()
    rs = upside.ewm(alpha=1 / period).mean() / downside.ewm(alpha=1 / period).mean()
    return 100*(1 - (1 + rs) ** -1)

def macd(price: 'pd.Series[pd.Float64Dtype]', fast: float, slow: float, signal: float) -> 'pd.Series[pd.Float64Dtype]':
    fm = price.ewm(span=fast, adjust=False).mean()
    sm = price.ewm(span=slow, adjust=False).mean()
    md = fm - sm
    signal = md - md.ewm(span=signal, adjust=False).mean()
    return signal

def generate_features(data):
    # Automatically-generated using pandas_ta
    df = data.copy()

    strategies = ['candles', 
                  'cycles', 
                  'momentum', 
                  'overlap', 
                  'performance', 
                  'statistics', 
                  'trend', 
                  'volatility', 
                  'volume']

    df.index = pd.DatetimeIndex(df.index)

    cores = os.cpu_count()
    df.ta.cores = cores

    for strategy in strategies:
        df.ta.study(strategy, exclude=['kvo'])

    df = df.set_index('date')

    # Generate all default indicators from ta library
    ta1.add_all_ta_features(data, 
                            'open', 
                            'high', 
                            'low', 
                            'close', 
                            'volume', 
                            fillna=True)

    # Naming convention across most technical indicator libraries
    data = data.rename(columns={'open': 'Open', 
                                'high': 'High', 
                                'low': 'Low', 
                                'close': 'Close', 
                                'volume': 'Volume'})
    data = data.set_index('date')

    # Custom indicators
    features = pd.DataFrame.from_dict({
        'dfast': data['Close'].rolling(window=10).std().abs(),
        'dmedium': data['Close'].rolling(window=50).std().abs(),
        'dslow': data['Close'].rolling(window=100).std().abs(),
        'fast': data['Close'].rolling(window=10).mean(),
        'medium': data['Close'].rolling(window=50).mean(),
        'slow': data['Close'].rolling(window=100).mean(),
        'ema_fast': ta1.trend.ema_indicator(data['Close'], window=5, fillna=True),
        'ema_medium': ta1.trend.ema_indicator(data['Close'], window=10, fillna=True),
        'ema_slow': ta1.trend.ema_indicator(data['Close'], window=64, fillna=True),
        'lr': np.log(data['Close']).diff().fillna(0),
        'rsi_5': rsi(data['Close'], period=5),
        'rsi_10': rsi(data['Close'], period=10),
        'rsi_100': rsi(data['Close'], period=100),
        'rsi_7': rsi(data['Close'], period=7),
        'rsi_28': rsi(data['Close'], period=28),
        'rsi_6': rsi(data['Close'], period=6),
        'rsi_14': rsi(data['Close'], period=14),
        'rsi_26': rsi(data['Close'], period=26),
        'macd_normal': macd(data['Close'], fast=12, slow=26, signal=9),
        'macd_short': macd(data['Close'], fast=10, slow=50, signal=5),
        'macd_long': macd(data['Close'], fast=200, slow=100, signal=50),
    })

    # Concatenate both manually and automatically generated features
    data = pd.concat([data, features], axis='columns').fillna(method='pad')

    # Remove potential column duplicates
    data = data.loc[:,~data.columns.duplicated()]

    # Revert naming convention
    data = data.rename(columns={'Open': 'open', 
                                'High': 'high', 
                                'Low': 'low', 
                                'Close': 'close', 
                                'Volume': 'volume'})

    # Concatenate both manually and automatically generated features
    data = pd.concat([data, df], axis='columns').fillna(method='pad')

    # Remove potential column duplicates
    data = data.loc[:,~data.columns.duplicated()]

    # A lot of indicators generate NaNs at the beginning of DataFrames, so remove them
    data = data.iloc[200:]
    data = data.reset_index(drop=False)

    return data

In [8]:
data = generate_features(data)
data.tail()

/usr/lib/python3.8/multiprocessing/pool.py:48: FutureWarning: The series.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  return list(map(*args))
/usr/local/lib/python3.8/dist-packages/ta/trend.py:769: RuntimeWarning: invalid value encountered in double_scalars
  dip[idx] = 100 * (self._dip[idx] / value)
/usr/local/lib/python3.8/dist-packages/ta/trend.py:774: RuntimeWarning: invalid value encountered in double_scalars
  din[idx] = 100 * (self._din[idx] / value)
/usr/local/lib/python3.8/dist-packages/ta/trend.py:938: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  self._psar_up = pd.Series(index=self._psar.index)
/usr/local/lib/python3.8/dist-packages/ta/trend.py:939: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence t

date          open         high      low         close  \
32521  2022-02-06 08:00 PM  41767.000000  41788.78777  41551.0  41618.346698   
32522  2022-02-06 09:00 PM  41619.214072  41752.00000  41594.0  41700.000000   
32523  2022-02-06 10:00 PM  41702.000000  41747.00000  41593.0  41641.000000   
32524  2022-02-06 11:00 PM  41637.000000  42739.00000  41549.0  42412.000000   
32525  2022-02-07 12:00 AM  42421.823872  42522.00000  41701.0  41778.000000   

         volume    volume_adi  volume_obv  volume_cmf     volume_fi  ...  \
32521   1592764  1.015417e+10 -4327771083    0.016497 -2.045909e+08  ...   
32522   1654274  1.015474e+10 -4326116809    0.018935 -1.560669e+08  ...   
32523   1828751  1.015405e+10 -4327945560    0.009885 -1.491854e+08  ...   
32524  33461774  1.016912e+10 -4294483786    0.179648  3.557702e+09  ...   
32525  10482068  1.016060e+10 -4304965854    0.062391  2.100083e+09  ...   

       EOM_14_100000000     MFI_14        NVI_1       PVI_1          PVOL  \
32521               inf  46.622844  1308.656612  953.332212  6.628820e+10   
32522               inf  46.158313  1308.656612  953.528407  6.898323e+10   
32523               inf  42.881379  1308.656612  953.386921  7.615102e+10   
32524               inf  64.705337  1308.656612  955.238461  1.419181e+12   
32525               inf  58.370353  1307.161752  955.238461  4.379198e+11   

       PVR           PVT     TSV_18_10    TSVs_18_10  TSVr_18_10  
32521  3.0 -1.874045e+10 -3.770370e+09 -2.835475e+09    1.329714  
32522  1.0 -1.874012e+10 -3.487293e+09 -3.197795e+09    1.090530  
32523  3.0 -1.874038e+10 -3.779410e+09 -3.572228e+09    1.057998  
32524  1.0 -1.867842e+10  2.196974e+10 -1.448692e+09  -15.165223  
32525  4.0 -1.869409e+10  1.547149e+10  6.952121e+08   22.254337  

[5 rows x 403 columns]

## Setup Trading Environment

In [9]:
from tensortrade.feed.core import DataFeed, Stream
from tensortrade.feed.core.base import NameSpace
from tensortrade.env.default.actions import ManagedRiskOrders
from tensortrade.env.default.rewards import RiskAdjustedReturns
from tensortrade.oms.orders import TradeType

bitstamp = Exchange("bitstamp", service=execute_order)(
    Stream.source(list(data["close"]), dtype="float").rename("USD-BTC")
)

portfolio = Portfolio(USD, [
    Wallet(bitstamp, 50000 * USD),
    Wallet(bitstamp, 1 * BTC)
])

with NameSpace("bitstamp"):
    features = [
        Stream.source(list(data[c]), 
                      dtype="float").rename(c) for c in data.columns[1:]
    ]

feed = DataFeed(features)
feed.compile()

renderer_feed = DataFeed([
    Stream.source(list(data["date"])).rename("date"),
    Stream.source(list(data["open"]), dtype="float").rename("open"),
    Stream.source(list(data["high"]), dtype="float").rename("high"),
    Stream.source(list(data["low"]), dtype="float").rename("low"),
    Stream.source(list(data["close"]), dtype="float").rename("close"), 
    Stream.source(list(data["volume"]), dtype="float").rename("volume") 
])

action_scheme = ManagedRiskOrders(stop=[0.06, 0.12, 0.18],
                                  take=[0.03, 0.06, 0.09],
                                  trade_sizes=4,
                                  durations=None,
                                  trade_type=TradeType.MARKET,
                                  order_listener=None,
                                  min_order_pct=0.06,
                                  min_order_abs=0.00)

reward_scheme = RiskAdjustedReturns(return_algorithm='sortino',
                                    window_size=1)

env = default.create(
    portfolio=portfolio,
    action_scheme=action_scheme,
    reward_scheme=reward_scheme,
    feed=feed,
    renderer_feed=renderer_feed,
    renderer=default.renderers.PlotlyTradingChart(),
    window_size=30
)

In [10]:
env.observer.feed.next()

{'internal': {'bitstamp:/USD-BTC': 7877.4,
  'bitstamp:/USD:/free': 50000.0,
  'bitstamp:/USD:/locked': 0.0,
  'bitstamp:/USD:/total': 50000.0,
  'bitstamp:/BTC:/free': 1.0,
  'bitstamp:/BTC:/locked': 0.0,
  'bitstamp:/BTC:/total': 1.0,
  'bitstamp:/BTC:/worth': 7877.4,
  'net_worth': 57877.4},
 'external': {'bitstamp:/open': 7897.3,
  'bitstamp:/high': 7898.8,
  'bitstamp:/low': 7849.8,
  'bitstamp:/close': 7877.4,
  'bitstamp:/volume': 9341499,
  'bitstamp:/volume_adi': -121951453.75854455,
  'bitstamp:/volume_obv': -153103304,
  'bitstamp:/volume_cmf': -0.17598308327563186,
  'bitstamp:/volume_fi': -154803883.140523,
  'bitstamp:/volume_em': -15867.367753290986,
  'bitstamp:/volume_sma_em': -1880.56000796242,
  'bitstamp:/volume_vpt': -31365.70231090398,
  'bitstamp:/volume_vwap': 7876.168494708246,
  'bitstamp:/volume_mfi': 30.389505331139944,
  'bitstamp:/volume_nvi': 1014.9341564847504,
  'bitstamp:/volatility_bbm': 7932.536,
  'bitstamp:/volatility_bbh': 8114.3356729809575,
  'b

## Setup and Train DQN Agent

In [11]:
n_steps = 1000
n_episodes = 10                 # Increase me!
window_size = 30
memory_capacity = n_steps * 10
save_path = 'agents/'

In [12]:
def get_optimal_batch_size(window_size=30, n_steps=1000, batch_factor=4, stride=1):
    """
    lookback = 30          # Days of past data (also named window_size).
    batch_factor = 4       # batch_size = (sample_size - lookback - stride) // batch_factor
    stride = 1             # Time series shift into the future.
    """
    lookback = window_size
    sample_size = n_steps
    batch_size = ((sample_size - lookback - stride) // batch_factor)
    return batch_size

batch_size = get_optimal_batch_size(window_size=window_size, n_steps=n_steps, batch_factor=4)
batch_size

242

In [13]:
agent = DQNAgent(env)

agent.train(batch_size=batch_size, 
            n_steps=n_steps, 
            n_episodes=n_episodes, 
            memory_capacity=memory_capacity, 
            save_path=save_path)

FigureWidget({
    'data': [{'close': array([7877.4, 7700. , 7605.4, ..., 6473.2, 6485. , 6473.8]),
          …

FigureWidget({
    'data': [{'close': array([7877.4 , 7700.  , 7605.4 , 7511.1 , 7489.1 , 7592.3 , 7586.8 , 76…

FigureWidget({
    'data': [{'close': array([7877.4 , 7700.  , 7605.4 , 7511.1 , 7489.1 , 7592.3 , 7586.8 , 76…

FigureWidget({
    'data': [{'close': array([7877.4 , 7700.  , 7605.4 , 7511.1 , 7489.1 , 7592.3 , 7586.8 , 76…

FigureWidget({
    'data': [{'close': array([7877.4, 7700. , 7605.4, ..., 7535.6, 7541.5, 7440. ]),
          …

...

FigureWidget({
    'data': [{'close': array([7877.4, 7700. , 7605.4, ..., 6251.1, 6266. , 6231.5]),
          …

FigureWidget({
    'data': [{'close': array([7877.4 , 7700.  , 7605.4 , ..., 6143.8 , 6133.09, 6141.6 ]),
    …

FigureWidget({
    'data': [{'close': array([7877.4, 7700. , 7605.4, ..., 6239.1, 6416.1, 6403.3]),
          …

FigureWidget({
    'data': [{'close': array([7877.4, 7700. , 7605.4, ..., 6336.2, 6338. , 6310.2]),
          …

-1797007.8147099216